# Experimentally determined Speed
File to parse and plot switch speed from experimental dataset. Raw data will be made available on request.
The impact framework was used to parse experimental data

In [1]:
import impact as                             impt
from impact.parsers import Parser as parser

impt.settings.perform_curve_fit = False
impt.settings.outlier_cleaning_flag = False
impt.settings.verbose = False
impt.settings.live_calculations = False
impt.settings.use_filtered_data = True

import numpy as np
from scipy.signal import savgol_filter as savgol
from scipy.interpolate import InterpolatedUnivariateSpline as interp
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from scipy.optimize import curve_fit
import pandas as pd
import copy
import pickle

import plotly as py
import plotly.graph_objs as go
import plotly.io as pio
pio.templates.default = "plotly_white"
from plotly.subplots import make_subplots
import sys
if 'ipykernel' in sys.modules:
    from plotly.offline import init_notebook_mode
    from plotly.offline import iplot as plot
    from IPython.display import HTML
    HTML(
        """
        <script>
            var waitForPlotly = setInterval( function() {
                if( typeof(window.Plotly) !== "undefined" ){
                    MathJax.Hub.Config({ SVG: { font: "STIX-Web" }, displayAlign: "center" });
                    MathJax.Hub.Queue(["setRenderer", MathJax.Hub, "SVG"]);
                    clearInterval(waitForPlotly);
                }}, 250 );
        </script>
        """
    )
    init_notebook_mode(connected=True)

colors = {'blues':['rgb(164,199,228)','rgb(119,171,214)','rgb(73,143,201)',
                   'rgb(49,113,165)','rgb(36,82,120)','rgb(23,52,76)'],
          'greens':['rgb(172,220,173)','rgb(130,203,133)','rgb(89,185,92)',
                    'rgb(63,152,66)','rgb(46,110,48)','rgb(28,67,29)'],
          'reds':['rgb(230,174,176)','rgb(218,133,137)','rgb(205,92,98)',
                  'rgb(187,57,64)','rgb(146,45,50)','rgb(104,32,35)'],
          'pinks':['rgb(215,181,210)','rgb(195,144,188)','rgb(175,107,165)',
                   'rgb(147,79,137)','rgb(110,59,102)','rgb(74,40,69)'],
          'browns':['rgb(216,197,184)','rgb(196,168,148)','rgb(176,139,112)',
                    'rgb(150,111,83)','rgb(115,85,63)','rgb(80, 59, 44)'],
          'oranges': ['rgb(255,206,146)','rgb(255,189,109)','rgb(255,173,73)',
                      'rgb(255,157,36)','rgb(255, 140, 0)','rgb(219,120,0)'],
          'cyans': ['rgb(177,222,219)','rgb(139,205,201)','rgb(100,189,183)',
                    'rgb(70,163,157)','rgb(53,124,120)','rgb(37,87,84)'],
          'yellows': ['rgb(244,239,186)','rgb(239,231,151)','rgb(233,224,116)',
                      'rgb(228,216,82)','rgb(223,208,47)','rgb(200,185,31)',],
          'blacks':['rgb(182,182,182)','rgb(146,146,146)','rgb(109,109,109)',
                    'rgb(73,73,73)','rgb(36,36,36)','rgb(0,0,0)']}

C:\Users\User\anaconda3\envs\impact\lib\site-packages\IPython\html.py:14: ShimWarning: The `IPython.html` package has been deprecated since IPython 4.0. You should import from `notebook` instead. `IPython.html.widgets` has moved to `ipywidgets`.
  "`IPython.html.widgets` has moved to `ipywidgets`.", ShimWarning)


In [2]:
font_defaults = dict(family='Myriad Pro', color='black', size=20)
axis_defaults = dict(ticks='outside', ticklen=6, tickangle=0, nticks=10, tickcolor='black', tickfont=font_defaults,
                     showline=True, linewidth=1, linecolor='black', mirror=True, zeroline=False,
                     title_font=font_defaults, title_standoff=2, showgrid=True)
stabilities = ['bistable', 'tet_stable', 'lac_stable', 'unstable']
stability_titles = {'bistable':'Bistable', 'tet_stable': 'Monostable Tet',
                    'lac_stable': 'Monostable Lac', 'unstable': 'Not Bistable'}
stability_colors = {'bistable': colors['blues'][2],
                    'tet_stable': colors['reds'][2],
                    'lac_stable': colors['greens'][2],
                    'unstable': colors['blacks'][2]}

def get_layout(analyte, ymax=10000, thresholds={'GFP':1000, 'mCherry':25}):
    layout=go.Layout(height=425, width=900, 
                      legend_font=font_defaults, legend_x=1.1, legend_y=1.05,

                      xaxis1={**dict(axis_defaults),**dict(title='Time (h)', side='bottom')},
                      xaxis2={**dict(axis_defaults),**dict(title='Time (h)', side='bottom')},
                      yaxis1={**dict(axis_defaults), 
                              **dict(title='OD700 (a.u.)')},
                      yaxis2={**dict(axis_defaults), 
                              **dict(title='Raw '+analyte+' (a.u.)', side='right')},
                      yaxis3={**dict(axis_defaults), 
                              **dict(title='Norm. '+analyte+' (a.u.)', range=(-ymax/50, 1.1*ymax))},
                      yaxis4={**dict(axis_defaults), 
                              **dict(title='Rate', side='right', range=(-1.1*thresholds[analyte], 1.1*thresholds[analyte]))})
    
    return layout


def gompertz(t, A, growth_rate, lag):
    return A*np.exp(-np.exp(growth_rate/A*np.e*(lag-t)+1))


def find_gomp_rate(time_vector, od_vector):
    A_init = 1
    growth_rate_init = 1.5
    lag_init = 2
    init_params = (A_init, growth_rate_init, lag_init)
    params, cov = curve_fit(f=gompertz,
                            xdata=time_vector,
                            ydata=od_vector,
                            p0=init_params, maxfev=10000,
                            bounds=([0.7, 0, 0], [1.5, 5, 8]), method='trf')
    
    return params[1]


def get_growth_rates(expt=None, strains=[]):
    gomp_rates = {}
    
    if strains == []:
        strains = [rep.trial_identifier.strain.name for rep in expt.replicate_trials
                           if rep.trial_identifier.strain.name not in ['lac', '0000', 'blank']]
        strains = sorted(strains, key=lambda x:[x[2:], x[:2]])
        
    for i, strain_name in enumerate(strains):
        if strain_name != 'lac':
            gomp_rates[strain_name] = {}
        rep = [rep for rep in expt.replicate_trials if rep.trial_identifier.strain.name == strain_name][0]
        trial_dict = rep.single_trial_dict

        for j, rep_id in enumerate(sorted(list(trial_dict))):
            analyte_dict = trial_dict[rep_id].analyte_dict
            time_vector = analyte_dict['OD700'].time_vector
            od_vector = analyte_dict['OD700'].data_vector
            
            if strain_name!='lac':
                gomp_rates[strain_name][rep_id] = find_gomp_rate(time_vector, od_vector)

    return gomp_rates


def get_switch_times(expt=None, strains=[], analyte='GFP', thresholds = {'GFP':1000, 'mCherry':25},
                     plot_fig=False, window_threshold=12, verbose=False):
    switch_times = dict()
    ymax=[]
    temp_colors = list(reversed(list(colors.values())))
    autofl_rep = [rep for rep in expt.replicate_trials if rep.trial_identifier.strain.name=='lac'][0]
    autofl_gfp_vector = autofl_rep.avg.analyte_dict['GFP'].data_vector
    mid_autofl_od = (max(autofl_rep.avg.analyte_dict['OD700'].data_vector) - min(autofl_rep.avg.analyte_dict['OD700'].data_vector))/2
    autofl_halftime_index = np.argmin(abs(autofl_rep.avg.analyte_dict['OD700'].data_vector-mid_autofl_od))

    if strains == []:
        strains = [rep.trial_identifier.strain.name for rep in expt.replicate_trials
                           if rep.trial_identifier.strain.name not in ['lac', '0000', 'blank']]
        strains = sorted(strains, key=lambda x:[x[2:], x[:2]])
        
    if plot_fig and len(strains)<10:
        fig = make_subplots(rows=1, cols=2, horizontal_spacing=0.25,
                            specs=[[{'secondary_y':True}, {'secondary_y':True}]])
    else:
        plot_fig=False

    for i, strain_name in enumerate(strains):
        if strain_name != 'lac':
            switch_times[strain_name] = {}
        rep = [rep for rep in expt.replicate_trials if rep.trial_identifier.strain.name == strain_name][0]
        trial_dict = rep.single_trial_dict

        for j, rep_id in enumerate(sorted(list(trial_dict))):
            analyte_dict = trial_dict[rep_id].analyte_dict
            time_vector = analyte_dict['OD700'].time_vector
            od_vector = analyte_dict['OD700'].data_vector
            fl_vector = analyte_dict[analyte].data_vector
            showlegend = [True if rep_id=='2' else False for temp in range(1)][0]

            if analyte=='GFP':
                mid_analyte_od = (max(od_vector)-min(od_vector))/2
                analyte_halftime_index = np.argmin(abs(od_vector-mid_analyte_od))
                t_offset = (analyte_halftime_index - autofl_halftime_index)*(analyte_halftime_index > autofl_halftime_index)
                
                if t_offset!=0:
                    adjusted_autofl_gfp_vector = np.concatenate((np.array([autofl_gfp_vector[0]]*t_offset), autofl_gfp_vector[:-t_offset]))
                else:
                    adjusted_autofl_gfp_vector = autofl_gfp_vector
                    
                norm_vector = savgol((fl_vector - adjusted_autofl_gfp_vector)/od_vector, window_length=5, polyorder=3)
            else:
                norm_vector = savgol(fl_vector/od_vector, window_length=5, polyorder=3)
            
            norm_vector[norm_vector<0] = 0
            rate_vector = np.gradient(norm_vector, time_vector)
    
            bools = [all(abs(rate_vector[j:j+window_threshold])<thresholds[analyte]) 
                               for j in range(len(rate_vector))]
        
            if not any(bools):
                index = len(rate_vector)-1
            else:
                index = np.argmax(bools)

            if index!=0 and index!= len(rate_vector)-1:
                slope = (rate_vector[index]-rate_vector[index-1])/(time_vector[index]-time_vector[index-1])
                switch_time = (thresholds[analyte]*(-slope)/abs(slope)-
                               rate_vector[index-1])/slope + time_vector[index-1]
            else:
                switch_time = time_vector[index]
                
            ymax.append(max(norm_vector[15:]))
            
            if strain_name!='lac':
                switch_times[strain_name][rep_id] = switch_time
                
            if plot_fig:
                fig.add_trace(go.Scatter(x=time_vector, y=od_vector, 
                                         name=strain_name, legendgroup=strain_name, showlegend=showlegend,
                                         mode='lines', line=dict(width=2, color=temp_colors[i][j*2], dash='dash', shape='spline')),
                              secondary_y=False, row=1, col=1)
                fig.add_trace(go.Scatter(x=time_vector, y=fl_vector, 
                                         name=strain_name, legendgroup=strain_name, showlegend=False,
                                         mode='lines', line=dict(width=2, color=temp_colors[i][j*2], shape='spline')),
                              secondary_y=True, row=1, col=1)

                if strain_name != 'lac':
                    fig.add_trace(go.Scatter(x=[switch_time]*10, y=np.linspace(-thresholds[analyte]*1.1,
                                                                               thresholds[analyte]*1.1, 10),
                                             name=strain_name, legendgroup=strain_name, showlegend=False, 
                                             mode='lines', line=dict(width=0.5, color='black', dash='solid')),
                                 secondary_y=True, row=1, col=2)
                    fig.add_trace(go.Scatter(x=time_vector, y=rate_vector,
                                             name=strain_name, legendgroup=strain_name, showlegend=False,
                                             mode='lines', line=dict(width=2, color=temp_colors[i][j*2], dash='dot')),
                                 secondary_y=True, row=1, col=2)
                    fig.add_trace(go.Scatter(x=time_vector, y=norm_vector,
                                             name=strain_name, legendgroup=strain_name, showlegend=False,
                                             mode='lines', line=dict(width=2, color=temp_colors[i][j*2], shape='spline')),
                                  secondary_y=False, row=1, col=2)

        if verbose and strain_name!='lac':
            print(strain_name, ': Mean - ', np.round(np.mean(list(switch_times[strain_name].values())), decimals=2),
                               ', Error - ', np.round(np.std(list(switch_times[strain_name].values()))/np.mean(list(switch_times[strain_name].values()))*100,
                                                      decimals=2), '%',  
                               'Raw Data - ', np.round(np.array(list(switch_times[strain_name].values())), decimals=2))

    if plot_fig:
        fig.update_layout(get_layout(analyte,max(ymax), thresholds))
        plot(fig)
        
    return switch_times

In [3]:
with open('pickled_data/speed_data.pickle', 'rb') as handle:
    expt_dict=pickle.load(handle)

In [4]:
stabilities = ['unstable', 'bistable']

rep_bistability_df = pd.read_csv('misc_excel_data/rep_bistability_df.csv')
rep_bistability_df['strain'] = rep_bistability_df['strain'].astype('str')
rep_bistability_df['stability'] = rep_bistability_df['stability'].apply(lambda x:stabilities[x=='bistable'])
rep_bistability_df = rep_bistability_df.set_index('strain')

st_bistability_df = pd.read_csv('misc_excel_data/st_bistability_df.csv')
st_bistability_df['strain'] = st_bistability_df['strain'].astype('str')
st_bistability_df['rep'] = st_bistability_df['rep'].astype('str')
st_bistability_df = st_bistability_df.set_index(['strain', 'rep'])
st_bistability_df['stability'] = st_bistability_df['stability'].apply(lambda x:stabilities[x=='bistable'])



deg_tags = ['No Tag', 'DAS Tag', 'DAS+2 Tag', 'LAA Tag']
deg_codes = {'0': '*', '1': 'DAS', '2':'DAS+2', '3':'LAA'}
rbs_codes = {'1':'A', '2':'B', '3': 'C', '4':'D', '5':'E'}

mche_df = pd.read_csv('misc_excel_data/mche_df.csv')
mche_df['tet_code'] = mche_df['tet_code'].astype('str')
mche_df = mche_df.set_index('tet_code')
mche_df = mche_df.loc[['21', '22', '30', '32', '33', '43', '50', '51', '52', '53']]
mche_df['deg_class'] = pd.qcut(mche_df['deg_mean'], 3, labels=['Low', 'Mid', 'High'])
mche_df['deg_tag'] = mche_df.index.map(lambda x:deg_tags[int(x[1])])

gfp_df = pd.read_csv('misc_excel_data/gfp_df.csv')
gfp_df['lac_code'] = gfp_df['lac_code'].astype('str')
gfp_df = gfp_df.set_index('lac_code')
gfp_df = gfp_df.loc[['10', '20', '21', '30', '33', '40', '42', '43', '52', '53']]
gfp_df['deg_class'] = pd.qcut(gfp_df['deg_mean'], 3, labels=['Low', 'Mid', 'High'])
gfp_df['deg_tag'] = gfp_df.index.map(lambda x:deg_tags[int(x[1])])

In [6]:
thresholds = {'GFP':1520, 'mCherry':60}
window_threshold = 50

expt = expt_dict['iptg']['plate_1']
strains = [rep.trial_identifier.strain.name for rep in expt.replicate_trials
                   if rep.trial_identifier.strain.name not in ['lac', '0000', 'blank']]

mcherrys = sorted(list(set([name[2:] for name in strains])), key=lambda x:x[1])
for mcherry in mcherrys:
    strain_list = sorted([strain for strain in strains if strain[2:]==mcherry])
    get_switch_times(expt=expt, strains=['lac']+strain_list[:8], analyte='mCherry',
                     plot_fig=True, window_threshold=window_threshold, thresholds=thresholds, verbose=True)
    get_switch_times(expt=expt, strains=['lac']+strain_list[:8], analyte='GFP',
                 plot_fig=True, window_threshold=window_threshold, thresholds=thresholds, verbose=True)


1030 : Mean -  4.41 , Error -  16.23 % Raw Data -  [3.4  4.93 4.9 ]
2030 : Mean -  5.28 , Error -  36.53 % Raw Data -  [3.78 4.05 8.  ]
2130 : Mean -  4.16 , Error -  19.19 % Raw Data -  [4.93 3.06 4.5 ]
3030 : Mean -  5.74 , Error -  27.89 % Raw Data -  [4.57 4.64 8.  ]
3330 : Mean -  5.92 , Error -  24.99 % Raw Data -  [4.71 5.04 8.  ]
4030 : Mean -  3.61 , Error -  0.85 % Raw Data -  [3.62 3.57 3.64]
4230 : Mean -  4.12 , Error -  8.98 % Raw Data -  [4.22 4.52 3.63]
4330 : Mean -  4.65 , Error -  6.31 % Raw Data -  [4.96 4.26 4.74]


1030 : Mean -  0.13 , Error -  141.42 % Raw Data -  [0.4 0.  0. ]
2030 : Mean -  0.53 , Error -  4.64 % Raw Data -  [0.5  0.56 0.54]
2130 : Mean -  0.6 , Error -  4.6 % Raw Data -  [0.56 0.63 0.59]
3030 : Mean -  2.83 , Error -  1.55 % Raw Data -  [2.79 2.82 2.89]
3330 : Mean -  2.5 , Error -  1.98 % Raw Data -  [2.43 2.53 2.55]
4030 : Mean -  3.42 , Error -  1.24 % Raw Data -  [3.37 3.41 3.47]
4230 : Mean -  3.2 , Error -  0.89 % Raw Data -  [3.16 3.2  3.23]
4330 : Mean -  3.17 , Error -  0.73 % Raw Data -  [3.16 3.16 3.21]


1021 : Mean -  2.57 , Error -  1.79 % Raw Data -  [2.52 2.63 2.56]
2021 : Mean -  2.6 , Error -  0.54 % Raw Data -  [2.61 2.58 2.61]
2121 : Mean -  2.71 , Error -  3.28 % Raw Data -  [2.8  2.59 2.74]
3021 : Mean -  2.61 , Error -  3.84 % Raw Data -  [2.5  2.74 2.58]
3321 : Mean -  2.91 , Error -  4.55 % Raw Data -  [3.1  2.83 2.8 ]
4021 : Mean -  2.73 , Error -  3.38 % Raw Data -  [2.85 2.63 2.72]
4221 : Mean -  2.85 , Error -  2.75 % Raw Data -  [2.93 2.88 2.74]
4321 : Mean -  2.95 , Error -  1.71 % Raw Data -  [3.   2.88 2.97]


1021 : Mean -  0.46 , Error -  64.61 % Raw Data -  [0.85 0.42 0.12]
2021 : Mean -  0.43 , Error -  70.88 % Raw Data -  [0.66 0.61 0.  ]
2121 : Mean -  0.38 , Error -  44.19 % Raw Data -  [0.16 0.42 0.56]
3021 : Mean -  1.69 , Error -  16.32 % Raw Data -  [1.31 1.81 1.96]
3321 : Mean -  1.33 , Error -  38.91 % Raw Data -  [0.62 1.51 1.85]
4021 : Mean -  2.43 , Error -  4.8 % Raw Data -  [2.29 2.41 2.57]
4221 : Mean -  2.67 , Error -  3.08 % Raw Data -  [2.56 2.69 2.76]
4321 : Mean -  2.74 , Error -  3.43 % Raw Data -  [2.62 2.75 2.85]


1032 : Mean -  1.87 , Error -  0.73 % Raw Data -  [1.86 1.89 1.87]
2032 : Mean -  2.01 , Error -  4.35 % Raw Data -  [2.06 2.09 1.89]
2132 : Mean -  2.02 , Error -  2.5 % Raw Data -  [1.98 2.09 1.99]
3032 : Mean -  1.85 , Error -  3.93 % Raw Data -  [1.94 1.76 1.84]


1032 : Mean -  0.22 , Error -  141.42 % Raw Data -  [0.   0.67 0.  ]
2032 : Mean -  0.61 , Error -  71.1 % Raw Data -  [0.97 0.86 0.  ]
2132 : Mean -  0.48 , Error -  10.29 % Raw Data -  [0.54 0.47 0.42]
3032 : Mean -  2.81 , Error -  5.36 % Raw Data -  [2.89 2.93 2.6 ]


1022 : Mean -  1.9 , Error -  0.46 % Raw Data -  [1.91 1.91 1.89]
2022 : Mean -  2.09 , Error -  1.88 % Raw Data -  [2.06 2.14 2.06]
2122 : Mean -  1.89 , Error -  7.17 % Raw Data -  [1.77 2.08 1.83]
3022 : Mean -  1.96 , Error -  4.2 % Raw Data -  [2.07 1.89 1.91]
3322 : Mean -  2.44 , Error -  2.73 % Raw Data -  [2.5  2.34 2.47]
4022 : Mean -  1.77 , Error -  4.03 % Raw Data -  [1.71 1.87 1.74]
4222 : Mean -  1.99 , Error -  6.8 % Raw Data -  [2.09 2.07 1.8 ]
4322 : Mean -  2.31 , Error -  4.26 % Raw Data -  [2.44 2.26 2.22]


1022 : Mean -  0.05 , Error -  141.42 % Raw Data -  [0.14 0.   0.  ]
2022 : Mean -  0.69 , Error -  41.93 % Raw Data -  [0.49 1.1  0.48]
2122 : Mean -  0.78 , Error -  40.48 % Raw Data -  [0.61 1.22 0.51]
3022 : Mean -  2.31 , Error -  8.16 % Raw Data -  [2.06 2.36 2.52]
3322 : Mean -  2.57 , Error -  3.08 % Raw Data -  [2.47 2.59 2.66]
4022 : Mean -  2.83 , Error -  3.29 % Raw Data -  [2.73 2.81 2.96]
4222 : Mean -  2.99 , Error -  2.36 % Raw Data -  [2.91 2.99 3.08]
4322 : Mean -  3.05 , Error -  2.55 % Raw Data -  [2.96 3.03 3.15]


In [9]:
transfer = {'iptg':'tet_to_lac', 'atc':'lac_to_tet'}
legend = {'iptg':'mcherry_to_gfp', 'atc':'gfp_to_mcherry'}
phase = []
lac = []
tet = []
rep_id = []
strain_name = []
gomp_growth_rate = []

for inducer in ['iptg', 'atc']:
    print(inducer)
    print(transfer[inducer], '_____', legend[inducer])

    for plate in ['plate_1', 'plate_2', 'plate_3', 'plate_4']:
        print(plate)
        expt = expt_dict[inducer][plate]
        strains = [rep.trial_identifier.strain.name for rep in expt.replicate_trials
                           if rep.trial_identifier.strain.name not in ['lac', '0000', 'blank']]
        
        for strain in strains:
            strain_name.extend([strain]*3)
            tet_times = get_switch_times(expt=expt, strains=[strain], analyte='mCherry',
                             plot_fig=False, window_threshold=window_threshold, thresholds=thresholds, verbose=False)
            lac_times = get_switch_times(expt=expt, strains=[strain], analyte='GFP',
                             plot_fig=False, window_threshold=window_threshold, thresholds=thresholds, verbose=False)
            rep_id.extend([key for key in sorted(lac_times[strain])])
            lac.extend([lac_times[strain][key] for key in sorted(lac_times[strain])])
            tet.extend([tet_times[strain][key] for key in sorted(tet_times[strain])])
            phase.extend([transfer[inducer]]*3)
            gomp_dict = get_growth_rates(expt=expt, strains=[strain])
            gomp_growth_rate.extend([gomp_dict[strain][key] for key in sorted(gomp_dict[strain])])

data_dict = {'strain': strain_name, 'rep': rep_id, 'phase':phase, 'laci':lac, 'tetr': tet,
             'growth_rate': gomp_growth_rate}
data_df = pd.DataFrame(data=data_dict)
data_df['rep']=data_df['rep'].replace(['4','5','6'],['1','2','3'])
data_df = data_df.sort_values(by=['phase', 'strain', 'rep'], ascending=[False,True,True],key=lambda x:x.apply(lambda y:(y[:2], y[2:])))

iptg_to_atc = pd.DataFrame(data_df[data_df['phase']=='tet_to_lac'])
iptg_to_atc = iptg_to_atc.set_index(['strain','rep'])
iptg_to_atc = iptg_to_atc.drop(['phase'], axis=1)
iptg_to_atc = iptg_to_atc.rename(columns={'laci':'lac_rise_i2a', 'tetr':'tet_fall_i2a',
                                          'growth_rate': 'growth_rate_i2a'})

atc_to_iptg = pd.DataFrame(data_df[data_df['phase']=='lac_to_tet'])
atc_to_iptg = atc_to_iptg.set_index(['strain', 'rep'])
atc_to_iptg = atc_to_iptg.drop(['phase'], axis=1)
atc_to_iptg = atc_to_iptg.rename(columns={'laci':'lac_fall_a2i', 'tetr':'tet_rise_a2i',
                                         'growth_rate': 'growth_rate_a2i'})

st_speed_df = pd.DataFrame(iptg_to_atc)
st_speed_df['lac_fall_a2i'] = atc_to_iptg['lac_fall_a2i']
st_speed_df['tet_rise_a2i'] = atc_to_iptg['tet_rise_a2i']
st_speed_df['growth_rate_a2i'] = atc_to_iptg['growth_rate_a2i']
st_speed_df = st_speed_df[['lac_rise_i2a', 'tet_fall_i2a', 'growth_rate_i2a',
                                   'lac_fall_a2i', 'tet_rise_a2i', 'growth_rate_a2i']]

rep_mean_speed_df = st_speed_df.mean(level=0)
rep_std_speed_df = st_speed_df.std(level=0)

iptg
tet_to_lac _____ mcherry_to_gfp
plate_1
plate_2
plate_3
plate_4
atc
lac_to_tet _____ gfp_to_mcherry
plate_1
plate_2
plate_3
plate_4


In [10]:
temp_colors = [colors['blues'][2], colors['blacks'][2], colors['blacks'][2], colors['blacks'][2]]
temp_dict = {'bistable': 0,
             'tet_stable': 1,
             'lac_stable': 2,
             'unstable': 3}
legend_dict = {'bistable':'Bistable', 'tet_stable': 'Monostable Tet',
               'lac_stable': 'Monostable Lac', 'unstable': 'Unstable'}

bistability_dfs = [st_bistability_df, rep_bistability_df]
speed_dfs = [st_speed_df, rep_mean_speed_df]
titles = ['Single Trials', 'Replicates']


In [11]:
for n, speed_df in enumerate(speed_dfs):

    plate = 'plate_2'

    tet_fall_0000 = list(get_switch_times(expt_dict['iptg'][plate], ['0000'], 'mCherry', plot_fig=False, window_threshold=window_threshold,
                          thresholds=thresholds, verbose=False)['0000'].values())
    lac_rise_0000 = list(get_switch_times(expt_dict['iptg'][plate], ['0000'], 'GFP', plot_fig=False, window_threshold=window_threshold,
                          thresholds=thresholds, verbose=False)['0000'].values())

    tet_rise_0000 = list(get_switch_times(expt_dict['atc'][plate], ['0000'], 'mCherry', plot_fig=False, window_threshold=window_threshold,
                          thresholds=thresholds, verbose=False)['0000'].values())
    lac_fall_0000 = list(get_switch_times(expt_dict['atc'][plate], ['0000'], 'GFP', plot_fig=False, window_threshold=window_threshold,
                          thresholds=thresholds, verbose=False)['0000'].values())

    fig = go.Figure()
    deg_rates = speed_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_mean']).values
    
    if n==0:
        x = tet_rise_0000
        y = tet_fall_0000
    else:
        x = [np.mean(tet_rise_0000)]
        y = [np.mean(tet_fall_0000)]
        
    fig.add_trace(go.Scatter(x=x, y=y, mode='markers', hoverinfo='text', hovertext=['0000']*3,
                             marker=dict(color=colors['greens'][4], symbol='x', size=10, opacity=0.8,
                                         line=dict(color='black', width=1)),
                             showlegend=False))

    fig.add_trace(go.Scatter(x=speed_df[['tet_rise_a2i']].max(axis=1).values,
                             y=speed_df[['tet_fall_i2a']].max(axis=1).values, 
                             mode='markers', hoverinfo='text', hovertext=list(speed_df.index), showlegend=False,
                             marker=dict(color=np.log10(deg_rates), 
                                         colorscale=py.colors.diverging.RdBu[1:4]+ py.colors.diverging.RdBu[-4:-1],
                                         opacity=0.8, size=8, line_color='black', line_width=0,
                                         colorbar=dict(title='Estimated Relative TetR Degradation Rate', titleside='right', 
                                                       ticktext=[1, 2, 5, 10, 20, 50, 100, 200],
                                                       tickvals=[np.log10(val) for val in [1, 2, 5, 10, 20, 50, 100, 200]],
                                                       titlefont=font_defaults, thickness=16, len=.9, ticks='outside', 
                                                       tickfont=font_defaults, tickcolor='black', outlinecolor='black', outlinewidth=1.25))))


    layout = go.Layout(height=450, width=440, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Tet Rise Time (Switching from LacI to TetR)', range=(-0.5,8.5))},
                       yaxis={**axis_defaults, **dict(title='Tet Fall Time (Switching from TetR to LacI)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)
    
#     if n==0:
#         pio.write_image(fig,"figures\degtag_effect_tet.svg",format='svg')




    fig = go.Figure()
    deg_rates = speed_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_mean']).values
    if n==0:
        x = lac_rise_0000
        y = lac_fall_0000
    else:
        x = [np.mean(lac_rise_0000)]
        y = [np.mean(lac_fall_0000)]
        

    fig.add_trace(go.Scatter(x=speed_df[['lac_rise_i2a']].max(axis=1).values,
                             y=speed_df[['lac_fall_a2i']].max(axis=1).values, 
                             mode='markers', hoverinfo='text', hovertext=list(speed_df.index), showlegend=False,
                             marker=dict(color=np.log10(deg_rates), 
                                         colorscale=py.colors.diverging.RdBu[1:4]+ py.colors.diverging.RdBu[-4:-1],
                                         opacity=0.8, size=8, line_color='black', line_width=0,
                                         colorbar=dict(title='Estimated Relative LacI Degradation Rate', titleside='right', 
                                                       ticktext=[1, 1.5, 2, 2.5, 3],
                                                       tickvals=[np.log10(val) for val in [1, 1.5, 2, 2.5, 3]],
                                                       titlefont=font_defaults, thickness=16, len=.9, ticks='outside', 
                                                       tickfont=font_defaults, tickcolor='black', outlinecolor='black', outlinewidth=1.25))))
    fig.add_trace(go.Scatter(x=x, y=y, mode='markers', hoverinfo='text', hovertext=['0000']*3,
                             marker=dict(color=colors['greens'][4], symbol='x', size=10, opacity=0.8,
                                         line=dict(color='black', width=1)),
                             showlegend=False))

    layout = go.Layout(height=450, width=440, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Lac Rise Time (Switching from TetR to LacI)', range=(-0.5,8.5))},
                       yaxis={**axis_defaults, **dict(title='Lac Fall Time (Switching from LacI to TetR)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)
#     if n==0:
#         pio.write_image(fig,"figures\degtag_effect_lac.svg",format='svg')



In [13]:
display(np.array(lac_fall_0000))
display(np.array(tet_rise_0000))

array([2.60373185, 2.5549993 , 2.21923286])

array([4.31174356, 4.54984561, 4.22014447])

In [16]:
(np.array(lac_fall_0000) + np.array(tet_rise_0000))/2

array([3.45773771, 3.55242245, 3.21968866])

In [20]:
for n, speed_df in enumerate(speed_dfs):

    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = ['rgb(216,14,14)','rgb(146,146,146)', 'rgb(5,130,193)']
    fig = go.Figure()
    tet_deg_rates = speed_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class']).values
    lac_deg_rates = speed_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class']).values

    
    x = (np.array(lac_fall_0000) + np.array(tet_rise_0000))/2
    y = (np.array(tet_fall_0000) + np.array(lac_rise_0000))/2
    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = speed_df[speed_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                                      mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]
    

            fig.add_trace(go.Scatter(x=temp_df[['lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1).values,
                                     y=temp_df[['tet_fall_i2a', 'lac_rise_i2a']].mean(axis=1).values,
                                     mode='markers', hoverinfo='text',
                                     hovertext=[value+'_i2a' for value in temp_df.index.get_level_values(0)],
                                     showlegend=True, name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                    marker=dict(color=marker_colors[j],
                                                symbol=symbols[i], size=10, opacity=0.8, line_width=0.5, line_color='black')))
    fig.add_trace(go.Scatter(x=x, y=y, mode='markers', hoverinfo='text', hovertext=['0000']*3,
                     marker=dict(color=colors['greens'][4], symbol='x', size=10, opacity=0.8,
                                 line=dict(color='black', width=1)),
                         showlegend=False))
    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Lac to Tet Switch Time (h)', range=(-0.5,8.5))},
                       yaxis={**axis_defaults, **dict(title='Tet to Lac Switch Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)


    if n==0:
        pio.write_image(fig,"figures\degtag_effect_binned_both.svg",format='svg')

In [614]:
for n, speed_df in enumerate(speed_dfs):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = ['rgb(216,14,14)','rgb(146,146,146)', 'rgb(5,130,193)']
    fig = go.Figure()
    tet_deg_rates = speed_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class']).values
    lac_deg_rates = speed_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class']).values

    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = speed_df[speed_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                                      mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]


            fig.add_trace(go.Scatter(x=temp_df['growth_rate_i2a'].values,
                                     y=temp_df[['tet_fall_i2a', 'lac_rise_i2a']].mean(axis=1).values,
                                     mode='markers', hoverinfo='text',
                                     hovertext=[value+'_i2a' for value in temp_df.index.get_level_values(0)],
                                     showlegend=True, name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                    marker=dict(color=marker_colors[j],
                                                symbol=symbols[i], size=10, opacity=0.8, line_width=0.5, line_color='black')))

    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Growth Rate (1/h)')},
                       yaxis={**axis_defaults, **dict(title='Tet to Lac Switching Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)
    
    if n==0:
        pio.write_image(fig,"figures\switch_time_vs_growth_degtags_tet_to_lac.svg",format='svg')
        
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = ['rgb(216,14,14)','rgb(146,146,146)', 'rgb(5,130,193)']
    fig = go.Figure()
    tet_deg_rates = speed_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class']).values
    lac_deg_rates = speed_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class']).values

    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = speed_df[speed_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                                      mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]


            fig.add_trace(go.Scatter(x=temp_df['growth_rate_a2i'].values,
                                 y=temp_df[['lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1).values,
                                 mode='markers', hoverinfo='text', hovertext=[value+'_a2i' for value in temp_df.index.get_level_values(0)],
                                 showlegend=True, name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                marker=dict(color=marker_colors[j],
                                            symbol=symbols[i], size=10, opacity=0.8, line_width=0.5, line_color='black')))


    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Growth Rate (1/h)')},
                       yaxis={**axis_defaults, **dict(title='Lac to Tet Switching Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)
    
    if n==0:
        pio.write_image(fig,"figures\switch_time_vs_growth_degtags_lac_to_tet.svg",format='svg')


In [617]:
for n, speed_df in enumerate(speed_dfs):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = ['rgb(216,14,14)','rgb(146,146,146)', 'rgb(5,130,193)']
    fig = go.Figure()
    tet_deg_rates = speed_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class']).values
    lac_deg_rates = speed_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class']).values

    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = speed_df[speed_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                                      mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]


            fig.add_trace(go.Scatter(x=temp_df[['growth_rate_i2a', 'growth_rate_a2i']].mean(axis=1).values,
                                     y=temp_df[['tet_fall_i2a', 'lac_rise_i2a', 'lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1).values,
                                     mode='markers', hoverinfo='text',
                                     hovertext=[value for value in temp_df.index],
                                     showlegend=True, name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                    marker=dict(color=marker_colors[j],
                                                symbol=symbols[i], size=10, opacity=0.8, line_width=0.5, line_color='black')))

    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Average Growth Rate (1/h)')},
                       yaxis={**axis_defaults, **dict(title='Average Switch Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    plot(fig)

#     if n==0:
#         pio.write_image(fig,"figures\switch_time_vs_growth_degtags_singletrials.svg",format='svg')
#     if n==1:
#         pio.write_image(fig,"figures\switch_time_vs_growth_degtags_replicates.svg",format='svg')


In [618]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs, speed_dfs)):
    time_ranges = [1,2,3,4,5,6,7,8]
    bistable_strains = []
    total_strains = []

    for threshold in time_ranges:
        indices = speed_df[(speed_df[['lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1)<threshold) & 
                   (speed_df[['tet_fall_i2a', 'lac_rise_i2a']].mean(axis=1)<threshold)].index
        total_strains.append(len(bistability_df.loc[indices]))
        try:
            bistable_strains.append(bistability_df.loc[indices]['stability'].value_counts()['bistable'])
        except KeyError:
            bistable_strains.append(0)
    cumulative_total_strains = np.array(total_strains)
    total_strains = np.diff(cumulative_total_strains, prepend=cumulative_total_strains[0])
    cumulative_bistable_strains = np.array(bistable_strains)
    bistable_strains = np.diff(cumulative_bistable_strains, prepend=cumulative_bistable_strains[0])
    fig = go.Figure()

    for stability in list(reversed(stabilities)):
        indices = bistability_df[bistability_df.stability==stability].index

        
        fig.add_trace(go.Scatter(x=speed_df.loc[indices][['lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1).values,
                                 y=speed_df.loc[indices][['lac_rise_i2a', 'tet_fall_i2a']].mean(axis=1).values,
                                 name=stability_titles[stability], legendgroup=stability, showlegend=True,
                                 mode='markers', hoverinfo='text', hovertext=list(speed_df.loc[indices].index),
                                 marker=dict(color=stability_colors[stability], size=8,
                                             opacity=0.8)))
    for k, threshold in enumerate(time_ranges):
        fig.add_annotation(x=0.5, y=threshold-0.5, text=str(bistable_strains[k])+'/'+str(total_strains[k]),
                           showarrow=False)

    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis=dict(title='IPTG to ATC Switch Time (Max of TetR Deg and LacI Prodn) (h)',
                                  title_standoff=0.5, type='linear',
                                  titlefont=dict(family='Myriad Pro', size=20, color='black'),
                                  showline=True, linewidth=1, linecolor='black', mirror=True, side='bottom',
                                  ticks='outside', ticklen=4, tickangle=0, nticks=8,
                                  tickfont=dict(size=20, family='Myriad Pro', color='black'), tickcolor='black',
                                  showgrid=True,zeroline=True),

                      yaxis=dict(title='ATC to IPTG Switch Time (Max of LacI Deg and TetR Prodn(h)',
                                titlefont=dict(family='Myriad Pro', size=20, color='black'),
                                type='linear',
                                  anchor='x', side='left', showgrid=True, zeroline=True,
                                tickfont=dict(family='Myriad Pro',size=20, color='black'), tickcolor='black', 

                                  showline=True, linewidth=1, linecolor='black', mirror=True,
                                  ticks='outside', ticklen=4, tickangle=0))
    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Lac to Tet Switch Time (h)', range=(-0.5,8.5))},
                       yaxis={**axis_defaults, **dict(title='Tet to Lac Switch Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    fig.update_annotations(font=font_defaults)

    plot(fig)

    if n==0:
        pio.write_image(fig,"figures\stability_time_both_singletrials.svg",format='svg')
        
    if n==1:
        pio.write_image(fig,"figures\stability_time_both_replicates.svg",format='svg')


In [619]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs, speed_dfs)):
    time_ranges = [1,2,3,4,5,6,7,8,9]
    bistable_strains = []
    total_strains = []

    for threshold in time_ranges:
        indices = speed_df[(speed_df[['lac_fall_a2i', 'tet_rise_a2i']].max(axis=1)<threshold) & 
                   (speed_df[['tet_fall_i2a', 'lac_rise_i2a']].max(axis=1)<threshold)].index
        total_strains.append(len(bistability_df.loc[indices]))
        try:
            bistable_strains.append(bistability_df.loc[indices]['stability'].value_counts()['bistable'])
        except KeyError:
            bistable_strains.append(0)
    cumulative_total_strains = np.array(total_strains)
    total_strains = np.diff(cumulative_total_strains, prepend=cumulative_total_strains[0])
    cumulative_bistable_strains = np.array(bistable_strains)
    bistable_strains = np.diff(cumulative_bistable_strains, prepend=cumulative_bistable_strains[0])
    fig = go.Figure()

    for stability in list(reversed(stabilities)):
        indices = bistability_df[bistability_df.stability==stability].index

        
        fig.add_trace(go.Scatter(x=speed_df.loc[indices][['lac_fall_a2i', 'tet_rise_a2i']].max(axis=1).values,
                                 y=speed_df.loc[indices][['lac_rise_i2a', 'tet_fall_i2a']].max(axis=1).values,
                                 name=stability_titles[stability], legendgroup=stability, showlegend=True,
                                 mode='markers', hoverinfo='text', hovertext=list(speed_df.loc[indices].index),
                                 marker=dict(color=stability_colors[stability], size=7,
                                             opacity=0.7)))
    for k, threshold in enumerate(time_ranges):
        fig.add_annotation(x=0.5, y=threshold-0.5, text=str(bistable_strains[k])+'/'+str(total_strains[k]),
                           showarrow=False)

    layout = go.Layout(height=500, width=525, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Lac to Tet Switch Time (h)', range=(-0.5,8.5))},
                       yaxis={**axis_defaults, **dict(title='Tet to Lac Switch Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    fig.update_annotations(font=font_defaults)

    plot(fig)
    if n==0:
        pio.write_image(fig,"figures\stability_time_both_singletrials_MAX.svg",format='svg')
        
    if n==1:
        pio.write_image(fig,"figures\stability_time_both_replicates_MAX.svg",format='svg')


In [636]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs, speed_dfs)):
    time_ranges = [1,2,3,4,5,6,7,8,9]
    bistable_strains = []
    total_strains = []
    fig = go.Figure()

    for stability in list(reversed(stabilities)):
        indices = bistability_df[bistability_df.stability==stability].index
        
        fig.add_trace(go.Scatter(x=speed_df.loc[indices][['growth_rate_i2a', 'growth_rate_a2i']].mean(axis=1).values,
                                 y=speed_df.loc[indices][['lac_rise_i2a', 'tet_fall_i2a',
                                                          'lac_fall_a2i', 'tet_rise_a2i']].mean(axis=1).values,
                                 name=stability_titles[stability], legendgroup=stability, showlegend=True,
                                 mode='markers', hoverinfo='text', hovertext=list(speed_df.loc[indices].index),
                                 marker=dict(color=stability_colors[stability], size=8, line_color='black',
                                             line_width=0.25, opacity=0.8)))

    layout = go.Layout(height=450, width=500, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Average Growth Rate (h)')},
                       yaxis={**axis_defaults, **dict(title='Average Switch Time (h)', range=(-0.5,8.5))})
    fig.update_layout(layout)
    fig.update_annotations(font=font_defaults)

    plot(fig)

    if n==0:
        pio.write_image(fig,"figures\Growth_Time_Stability_SingleTrials.svg",format='svg')
        
    if n==1:
        pio.write_image(fig,"figures\Growth_Time_Stability_Replicates.svg",format='svg')

In [561]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs, speed_dfs)):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = [py.colors.diverging.RdBu[1],colors['blacks'][1], py.colors.diverging.RdBu[-2]]   
    pca_inputs_df = pd.DataFrame(speed_df)
    pca_inputs_df['tet_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_mean'])
    pca_inputs_df['lac_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_mean'])
    pca_inputs_df['tet_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class'])
    pca_inputs_df['lac_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class'])
    input_features = ['lac_rise_i2a', 'tet_fall_i2a', 'lac_fall_a2i', 'tet_rise_a2i']
    x = pca_inputs_df[input_features].values
    y = speed_df.index.get_level_values(0).values
    x = StandardScaler().fit_transform(x)

    pca=PCA(n_components=4)
    pcs = pca.fit_transform(x)
    principal_df = pd.DataFrame(data=pcs[:,:2], columns = ['PC1', 'PC2'], index=pca_inputs_df.index)

    pca_df = pca_inputs_df.copy(deep=True)
    pca_df = pd.concat([pca_df,principal_df], axis=1)

    fig_scores = go.Figure()

    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = pca_df[pca_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                            mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]


            fig_scores.add_trace(go.Scatter(x=temp_df['PC1'], y=temp_df['PC2'],
                                     mode='markers', hoverinfo='text', hovertext=list(temp_df.index.values), showlegend=True, 
                                     name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                    marker=dict(color=marker_colors[j], symbol=symbols[i], size=8, opacity=0.7, 
                                                line_width=0.25, line_color='black')))

    layout = go.Layout(height=450, width=490, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Principal Component 1', zeroline=True, zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(title='Principal Component 2', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_scores.update_layout(layout)
    plot(fig_scores)

    fig_loadings = go.Figure()
    for k, feature in enumerate(input_features):
        fig_loadings.add_trace(go.Scatter(x=[0]+[pca.components_[0,k]],
                                         y=[0]+[pca.components_[1,k]],
                                         mode='lines', showlegend=False,
                                         line=dict(width=1.5, color='rgb(54, 146, 68)'),
                                         name=feature))

    layout = go.Layout(height=450, width=425, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(range=(-0.65, 0.05), title='Principal Component 1', zeroline=True, zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(range=(-1,1), title='Principal Component 2', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_loadings.update_layout((layout))
    plot(fig_loadings)


    fig_expvar = go.Figure()

    fig_expvar.add_trace(go.Scatter(x=np.arange(1,5),
                                 y=np.cumsum(pca.explained_variance_ratio_)*100,
                                 mode='lines+markers',
                                 line=dict(width=1.5, color='rgb(33,100,175)'),
                                 name=analyte))
    layout = go.Layout(height=450, width=425, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Number of Principal Components', zeroline=True, 
                                                      zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(title='% Variance Explained', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_expvar.update_layout((layout))
    plot(fig_expvar)


In [562]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs, speed_dfs)):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = [py.colors.diverging.RdBu[1],colors['blacks'][1], py.colors.diverging.RdBu[-2]]   
    pca_inputs_df = pd.DataFrame(speed_df)
    pca_inputs_df['tet_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_mean'])
    pca_inputs_df['lac_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_mean'])
    pca_inputs_df['tet_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class'])
    pca_inputs_df['lac_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class'])
    input_features = ['lac_rise_i2a', 'tet_fall_i2a', 'lac_fall_a2i', 'tet_rise_a2i']
    x = pca_inputs_df[input_features].values
    y = speed_df.index.get_level_values(0).values
    x = StandardScaler().fit_transform(x)

    pca=PCA(n_components=4)
    pcs = pca.fit_transform(x)
    principal_df = pd.DataFrame(data=pcs[:,:2], columns = ['PC1', 'PC2'], index=pca_inputs_df.index)

    pca_df = pca_inputs_df.copy(deep=True)
    pca_df = pd.concat([pca_df,principal_df], axis=1)

    fig_scores = go.Figure()

    for stability in list(reversed(stabilities)):
        indices = bistability_df[bistability_df.stability==stability].index

        fig_scores.add_trace(go.Scatter(x=pca_df.loc[indices]['PC1'],
                                 y=pca_df.loc[indices]['PC2'],
                                 name=stability_titles[stability], legendgroup=stability, showlegend=True,
                                 mode='markers', hoverinfo='text', hovertext=list(speed_df.loc[indices].index),
                                 marker=dict(color=stability_colors[stability], size=7,
                                             opacity=0.7)))

    layout = go.Layout(height=450, width=490, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Principal Component 1', zeroline=True)},
                       yaxis={**axis_defaults, **dict(title='Principal Component 2', zeroline=True)})
    fig_scores.update_layout(layout)
    plot(fig_scores)



In [22]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs[:1], speed_dfs[:1])):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = ['rgb(216,14,14)','rgb(146,146,146)', 'rgb(5,130,193)']
    pca_inputs_df = pd.DataFrame(speed_df)
    pca_inputs_df['tet_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_mean'])
    pca_inputs_df['lac_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_mean'])
    pca_inputs_df['tet_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class'])
    pca_inputs_df['lac_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class'])
    input_features = ['lac_rise_i2a', 'tet_fall_i2a', 'lac_fall_a2i', 'tet_rise_a2i', 'growth_rate_i2a', 'growth_rate_a2i']
    x = pca_inputs_df[input_features].values
    y = speed_df.index.get_level_values(0).values
    x = StandardScaler().fit_transform(x)

    pca=PCA(n_components=4)
    pcs = pca.fit_transform(x)
    principal_df = pd.DataFrame(data=pcs[:,:2], columns = ['PC1', 'PC2'], index=pca_inputs_df.index)

    pca_df = pca_inputs_df.copy(deep=True)
    pca_df = pd.concat([pca_df,principal_df], axis=1)

    fig_scores = go.Figure()

    for i, lac_deg in enumerate(['Low', 'Mid', 'High']):
        for j,tet_deg in enumerate(['Low', 'Mid', 'High']):
            temp_df = pca_df[pca_df.index.get_level_values(0).map(lambda x:(gfp_df.loc[x[:2]]['deg_class'], 
                                                                            mche_df.loc[x[2:]]['deg_class']))==(lac_deg, tet_deg)]


            fig_scores.add_trace(go.Scatter(x=temp_df['PC1'], y=temp_df['PC2'],
                                     mode='markers', hoverinfo='text', hovertext=list(temp_df.index.values), showlegend=True, 
                                     name=lac_deg+', '+tet_deg, legendgroup=lac_deg+', '+tet_deg,
                                    marker=dict(color=marker_colors[j], symbol=symbols[i], size=10, opacity=0.8, 
                                                line_width=0.25, line_color='black')))

    layout = go.Layout(height=450, width=490, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Principal Component 1', zeroline=True, zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(title='Principal Component 2', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_scores.update_layout(layout)
    plot(fig_scores)

    fig_loadings = go.Figure()
    for k, feature in enumerate(input_features):
        fig_loadings.add_trace(go.Scatter(x=[0]+[pca.components_[0,k]],
                                         y=[0]+[pca.components_[1,k]],
                                         mode='lines', showlegend=False,
                                         line=dict(width=1.5, color='rgb(54, 146, 68)'),
                                         name=feature))

    layout = go.Layout(height=450, width=425, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(range=(-0.6, 0.6), title='Principal Component 1', zeroline=True, zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(range=(-0.5,1), title='Principal Component 2', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_loadings.update_layout((layout))
    plot(fig_loadings)


    fig_expvar = go.Figure()

    fig_expvar.add_trace(go.Scatter(x=np.arange(1,5),
                                 y=np.cumsum(pca.explained_variance_ratio_)*100,
                                 mode='lines+markers',
                                 line=dict(width=1.5, color='rgb(33,100,175)'),
                                 name=analyte))
    layout = go.Layout(height=450, width=425, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Number of Principal Components', zeroline=True, 
                                                      zerolinecolor='black', zerolinewidth=1)},
                       yaxis={**axis_defaults, **dict(title='% Variance Explained', zeroline=True, zerolinecolor='black', zerolinewidth=1)})
    fig_expvar.update_layout((layout))
    plot(fig_expvar)
    
# if n==0:
#     pio.write_image(fig_scores,"figures\PCAScores_degs_growth.svg",format='svg')
#     pio.write_image(fig_loadings,"figures\PCALoadings_degs_growth.svg",format='svg')
#     pio.write_image(fig_expvar,"figures\PCAExpVar_degs_growth.svg",format='svg')

NameError: name 'analyte' is not defined

In [29]:
for k, feature in enumerate(input_features):
    print(feature, pca.components_[0,k], pca.components_[1,k])
    

lac_rise_i2a 0.15347631617628626 0.9323772012805813
tet_fall_i2a 0.43613698407160834 -0.34295585798130185
lac_fall_a2i 0.39608028980551147 0.07968247201812541
tet_rise_a2i 0.4776458514528405 -0.0761711000517026
growth_rate_i2a -0.4413011965136492 -0.029771407478613482
growth_rate_a2i -0.45437611080576434 0.004045302860785144


In [638]:
for n, (bistability_df, speed_df) in enumerate(zip(bistability_dfs[:1], speed_dfs[:1])):
    symbols = ['triangle-down', 'circle', 'triangle-up']
    marker_colors = [py.colors.diverging.RdBu[1],colors['blacks'][1], py.colors.diverging.RdBu[-2]]   
    pca_inputs_df = pd.DataFrame(speed_df)
    pca_inputs_df['tet_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_mean'])
    pca_inputs_df['lac_deg_rate'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_mean'])
    pca_inputs_df['tet_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:mche_df.loc[x[2:]]['deg_class'])
    pca_inputs_df['lac_deg_class'] = pca_inputs_df.index.get_level_values(0).map(lambda x:gfp_df.loc[x[:2]]['deg_class'])
    input_features = ['lac_rise_i2a', 'tet_fall_i2a', 'lac_fall_a2i', 'tet_rise_a2i', 'growth_rate_i2a', 'growth_rate_a2i']
    x = pca_inputs_df[input_features].values
    y = speed_df.index.get_level_values(0).values
    x = StandardScaler().fit_transform(x)

    pca=PCA(n_components=4)
    pcs = pca.fit_transform(x)
    principal_df = pd.DataFrame(data=pcs[:,:2], columns = ['PC1', 'PC2'], index=pca_inputs_df.index)

    pca_df = pca_inputs_df.copy(deep=True)
    pca_df = pd.concat([pca_df,principal_df], axis=1)

    fig_scores = go.Figure()

    for stability in list(reversed(stabilities)):
        indices = bistability_df[bistability_df.stability==stability].index

        fig_scores.add_trace(go.Scatter(x=pca_df.loc[indices]['PC1'],
                                 y=pca_df.loc[indices]['PC2'],
                                 name=stability_titles[stability], legendgroup=stability, showlegend=True,
                                 mode='markers', hoverinfo='text', hovertext=list(speed_df.loc[indices].index),
                                 marker=dict(color=stability_colors[stability], size=8, line_color='black', line_width=0.25,
                                             opacity=0.7)))

    layout = go.Layout(height=450, width=490, legend_font=font_defaults, title=titles[n], title_font=font_defaults,
                       xaxis={**axis_defaults, **dict(title='Principal Component 1', zeroline=True)},
                       yaxis={**axis_defaults, **dict(title='Principal Component 2', zeroline=True)})
    fig_scores.update_layout(layout)
    plot(fig_scores)
    if n==0:
        pio.write_image(fig_scores,"figures\PCAScores_stabilities_growth.svg",format='svg')

In [35]:
mche_df.to_csv('final_mche.csv')

In [34]:
gfp_df.to_csv('final_gfp.csv')